# Hw 2 Part 1:
#Topic Modeling using LDA
---



In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/gdrive


In [ ]:
import re
import numpy as np
import pandas as pd
import os

# Gensim
import gensim
from gensim.utils import simple_preprocess
import gensim.corpora as corpora
from gensim.models import CoherenceModel
from gensim.models import ldaseqmodel
from gensim.test.utils import datapath

# stopwords
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('stopwords') 

# spacy for lemmatization
import spacy

# modeling
from sklearn.model_selection import train_test_split

# Plotting tools
!pip install pyLDAvis
import pyLDAvis
import pyLDAvis.gensim 
import matplotlib.pyplot as plt
%matplotlib inline
from pprint import pprint

# Set up log to terminal
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

#!pip install playsound
#from playsound import playsound

from datetime import datetime, date

path = r'/content/gdrive/My Drive/Colab_Datasets'
os.chdir(path)

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


# *Stratified Sampling*

In [ ]:
df = pd.read_excel('Index_fund_all.xlsx')
df = df.dropna(axis=0)
n = 389
df = df.groupby('filing_year').apply(lambda x: x.sample(n=n))    #[389, 504, 579, 619, 628, 636, 705, 810, 891]
df = df.reset_index(drop=True)
df = pd.DataFrame(df)
#print(df)

# *Regular Sampling*

In [ ]:
df = pd.read_excel('Index_fund_all.xlsx')
df = df.dropna(axis=0)

# *Data PreProcessing*

In [ ]:
df1 = df.principal_strategies
df2 = df1.values.tolist()

def sentence_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(sentence.lower(), deacc=True))  # deacc=True removes punctuations

df3 = list(sentence_to_words(df2))

# Removing Stop Words
stop_words = stopwords.words('english')
stop_words.extend(['from', 'subject', 're', 'edu', 'use','index','fund'])

def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

df4 = remove_stopwords(df3)

# Lemmatization
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

nlp = spacy.load('en', disable=['parser', 'ner'])

df5 = lemmatization(df4, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])

dict = corpora.Dictionary(df5)

df6 = df5.copy()
corpus = [dict.doc2bow(word) for word in df5]
print('Number of unique tokens: %d' % len(dict))
print('Number of documents: %d' % len(corpus))

2019-11-11 18:44:10,988 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2019-11-11 18:44:11,828 : INFO : built Dictionary(4403 unique tokens: ['achieve', 'add', 'aim', 'anticipated', 'approach']...) from 5761 documents (total 1462577 corpus positions)


Number of unique tokens: 4403
Number of documents: 5761


# Fitting the Model

In [ ]:
starttime = datetime.now()

train_corpus, test_corpus = train_test_split(corpus, train_size=0.8)

def compute_loglikelihood_values(dictionary, df, train, test, limit, start, step, passes):
    coherence_values = []
    likelihood_values = []
    model_list = []
    
    for num_topics in range(start, limit, step):
        model = gensim.models.ldamodel.LdaModel(corpus=train,
                                                id2word=dictionary,
                                                num_topics=num_topics, 
                                                random_state=100,
                                                passes=passes,
                                                alpha='auto',
                                                per_word_topics=False)
        
        model_list.append(model)

        likelihood_values.append(model.log_perplexity(test))

        coherencemodel = CoherenceModel(model=model, 
                                        texts=df6, 
                                        dictionary=dictionary, 
                                        coherence='c_v')
        
        coherence_values.append(coherencemodel.get_coherence())
    
    return model_list, likelihood_values, coherence_values


start = 10 
limit = 40
step  = 1
passes = 50

model_list, likelihood_values, coherence_values = compute_loglikelihood_values(dictionary=dict, 
                                                                               df=df6,
                                                                               train=train_corpus,
                                                                               test=test_corpus, 
                                                                               limit=limit,
                                                                               start=start,
                                                                               step=step,
                                                                               passes=passes)

stoptime = datetime.now()
################################################################################
print('')
print('')
print('')
print('')
print('')
# Score Charts
fig, ax1 = plt.subplots()
plt.title('LDA Topic Modeling - Score Chart')
# Log Likelihood Plot
x = range(start, limit, step)
color = 'tab:red'
ax1.set_xlabel('No. of Topics')
ax1.set_ylabel('Log Liklihood Score', color=color)
ax1.plot(x, likelihood_values, color=color)
ax1.tick_params(axis='y', labelcolor=color)

# Coherence Plot
ax2 = ax1.twinx()  # instantiate a second axes that shares the same x-axis

color = 'tab:blue'
ax2.set_ylabel('Coherence Score', color=color)  
ax2.plot(x, coherence_values, color=color)
ax2.tick_params(axis='y', labelcolor=color)

fig.tight_layout()  # otherwise the right y-label is slightly clipped
plt.show()

# Model Metrics
# Parameters
print('Parameters')
date = date.today()
d2 = date.strftime("%B %d, %Y")
print('Date:{}'.format(d2))
print('Range: {}:{}:{}'.format(start,step,limit))
print('Number of unique tokens: %d' % len(dict))
print('Stratified Sample Group Size: %d' % n)
print('Number of documents: %d' % len(corpus))
print('Number of passes: %d' % passes)
#startdt_string = starttime.strftime("%d/%m/%Y %H:%M:%S")
#stopdt_string = stoptime.strftime("%d/%m/%Y %H:%M:%S")
runtime = stoptime - starttime
print('Runtime:{}'.format(runtime))


# Optimal Models
z = pd.DataFrame({'Topics':x, 'Coherence_values':coherence_values, 'Log_Liklihood_Score':likelihood_values})

x11 = z.loc[z.Coherence_values.idxmax(), 'Topics']
x12 = round(z['Coherence_values'].max(), 2)
print('')
print('Optimal Coherent Model')
print('Coherency score: {}'.format(x12))
print('# of Topics: %d' % x11)

x21 = z.loc[z.Log_Liklihood_Score.idxmin(), 'Topics']
x22 = round(z['Log_Liklihood_Score'].min(),2)
print('')
print('Optimal Log-Liklihood Model')
print('Log-Liklihood score: {}'.format(x22))
print('# of Topics: %d' % x21)
print('')
print('')
print('')
print('')
print('')

2019-11-11 18:45:06,933 : INFO : using autotuned alpha, starting with [0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1]
2019-11-11 18:45:06,934 : INFO : using symmetric eta at 0.1
2019-11-11 18:45:06,937 : INFO : using serial LDA version on this node
2019-11-11 18:45:06,948 : INFO : running online (multi-pass) LDA training, 10 topics, 50 passes over the supplied corpus of 4608 documents, updating model once every 2000 documents, evaluating perplexity every 4608 documents, iterating 50x with a convergence threshold of 0.001000
2019-11-11 18:45:06,949 : INFO : PROGRESS: pass 0, at document #2000/4608
2019-11-11 18:45:08,491 : INFO : optimized alpha [0.13606231, 0.12127513, 0.15225995, 0.16112518, 0.15033689, 0.1702337, 0.12685855, 0.15603995, 0.14288314, 0.13859007]
2019-11-11 18:45:08,493 : INFO : merging changes from 2000 documents into a model of 4608 documents
2019-11-11 18:45:08,503 : INFO : topic #1 (0.121): 0.028*"security" + 0.020*"market" + 0.018*"include" + 0.015*"company" + 0

KeyboardInterrupt: ignored

# Bubble Charts

In [ ]:
#dictionary = gensim.corpora.Dictionary.load('dictionary.gensim')
#corpus = pickle.load(open('corpus.pkl', 'rb'))
#lda = gensim.models.ldamodel.LdaModel.load('model5.gensim')
#import pyLDAvis.gensim
lda_display = pyLDAvis.gensim.prepare(model_list[0], corpus, dict, sort_topics=False)
pyLDAvis.display(lda_display)